In [1]:
import requests
import requests.auth
from json import load
from praw import Reddit
from textblob import TextBlob
from collections import deque
from pandas import DataFrame,Series,to_datetime,read_csv
creds = {}
with open('/home/justin/.local/cache/reddit/info','r') as credentials:
    creds = load(credentials)
client_auth = requests.auth.HTTPBasicAuth(creds['ID'],creds['SECRET'])
post_data = {'grant_type':'password','username':creds['USER'],'password':creds['PASS']}
headers = {'User-Agent':creds['AGENT']}
response = requests.post('https://www.reddit.com/api/v1/access_token',auth=client_auth,data=post_data,headers=headers)
response.json()
token = response.json()['access_token']

headers = {"Authorization": token, "User-Agent": creds['AGENT']}
response = requests.get("https://oauth.reddit.com/api/v1/me", headers=headers)

reddit = Reddit(client_id=creds['ID'],
                client_secret=creds['SECRET'],
                user_agent = creds['AGENT'],
                username = creds['USER'],
                password = creds['PASS'])

searched_subs = ['AntiLGBTQIA','againsttrans','DiversityNews','hardunpopularopinon','thereareonly2genders','pics','justiceserved','metacanada']

not_conditions = ['jig is up','great ape']
slurs = ['ching chong','chink','christ-killer','christ killer','gook','goy','half-breed', 'half breed', 'heeb','hebe','kike','jewboy','jigaboo','jiggabo', 'jig', 'jigga', 'jigger', 'jungle bunny','kyke','niglet','nig-nog', 'nig nog', 'nignog','nigger','nigga', 'nigress','niggah', 'nigga','porch monkey','raghead','rag head', 'sambo','shylock','slant-eye', 'slant eye','spic','spick','spik','tar baby','tar-baby','tyrone','towel head', 'uncle tom','wetback','beaner','camel jockey','coon-ass', 'coon','539','1488', '10%','tnb','yard ape','welfare queen', 'unemployus', 'toucan sam','three-fifth','three fifths', 'three fifth', 'three-fifths','point six', 'point-six', '36-30', 'thirty-six-thirty', 'thirty-six thirty','thirtysix-thirty','thirtysix thirty','satchmo','sambo','race traitor','race-traitor','mammy','pickaninny','sheboon','furfag','chimpout']
questionable = ['natsee','pattern-recognition', 'pattern recognition']
len(slurs)

76

In [2]:
existing_subreddit_scrapes= read_csv('../data/comment_info_final.csv')
comment_ids = set(existing_subreddit_scrapes['comment_id'].tolist())
len(comment_ids)-existing_subreddit_scrapes.shape[0]
del existing_subreddit_scrapes['Unnamed: 0']

/home/justin/.local/opt/anaconda2/envs/galvanize/lib/python3.7/site-packages/IPython/core/interactiveshell.py:3058: DtypeWarning: Columns (0) have mixed types. Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


In [3]:
from copy import deepcopy
def build_dataframe(comment, df, directory='/home/justin/.local/share/xdg/media/documents/textfiles/galvanize/slur-prediction/data',filename='comment_info'):
    '''
    Takes Reddit Comment object and puts relevent attributes 
    into a dictionary that will be used to create a DataFrame.  
    The DataFrame will then be used to create a csv file for
    storage.
    
    Parameters:
    -----------
    
    comment: Reddit Comment instance
    df: dict
    directory: str
    filename: str
    
    Returns:
    --------
    
    None
    '''
    #df['reference_set'].add(comment.id)
    if not comment.author:
        df['author'].append('None')
    else:
        df['author'].append(comment.author.name)
    df['body'].append(comment.body)
    df['subreddit'].append(comment._submission.subreddit.display_name)
    df['sub_id'].append(comment._submission.id)
    df['url'].append(comment._submission.url)
    df['comment_id'].append(comment.id)
    df['comment_permalink'].append(comment.permalink)
    df['submission_permalink'].append(comment._submission.permalink)
    
    '''
    After any of the lists that are stored as dictionary values
    have grown by some integer multiple of 500, create a DataFrame
    from the dictionary and save it to a csv file.
    '''
    if len(df['author']) % 500 == 0:
        ##l = len(df['author'])//500
       ## backup = df['reference_set']
       # del df['reference_set']
        DataFrame(df).to_csv(f'{directory}/{filename}_user_new.csv')
        #df['reference_set'] = backup
        #del backup

def parse_comment_forest(CommentForest, df1,deq):
    '''
    Takes a CommentForest instance, adds the top-level comments
    to a dictionary where the comments and other possibly-useful
    information is stored, and adds the replies (another instance
    of CommentForest) to a queue for later processing
    
    Parameters:
    -----------
    
    CommentForest: Reddit CommentForest
    df1: dict
    deq: collections.deque
    '''
    CommentForest.replace_more(limit=None)
    author_len = len(df1['author'])
    for comment in CommentForest.list():
        if len(df1['author']) > author_len + 25:
            author_len = len(df1['author'])
            print(comment.body,end=' -|-+-|- ')
            print(author_len, ' -|-+-|- ', len(deq))
        if comment.id not in comment_ids:
            comment_ids.add(comment.id)
            build_dataframe(comment, df1, filename='problematic')
            deq.append(comment.replies)



In [23]:
directory='/home/justin/.local/share/xdg/media/documents/textfiles/galvanize/slur-prediction/data'
filename='redditor_scrape'
DataFrame(problematic).to_csv(f'{directory}/{filename}.csv')

In [3]:
from copy import deepcopy
from collections import deque
info = {'author':[], 'url':[],'body':[],'subreddit':[],
        'sub_id':[],'comment_id':[],'comment_permalink':[],
        'submission_permalink':[]}
problematic,backup, backup_info = deepcopy(info),deepcopy(info),deepcopy(info)
queue = deque()

In [10]:
def sub_cont(sub):
    return reddit.subreddit(sub).controversial()
def sub_hot(sub):
    return reddit.subreddit(sub).hot()
def sub_new(sub):
    return reddit.subreddit(sub).new()
def sub_top(sub):
    return reddit.subreddit(sub).top()
x = lambda sub: reddit.subreddit(sub).controversial()
x('news')

In [21]:
def scrape_subreddits(searched_subs, reddit, dictionary, queue):
    sorting_methods = \
        [ lambda sub: reddit.subreddit(sub).hot(),
          lambda sub: reddit.subreddit(sub).new(),
          lambda sub: reddit.subreddit(sub).top(),
          lambda sub: reddit.subreddit(sub).controversial() ]

    for subreddit in searched_subs:
        for sorting in sorting_methods:
            for submission in sorting(subreddit):
                parse_comment_forest(submission.comments,\
                                        dictionary,queue)
        while len(queue) >= 1:
            parse_comment_forest(queue.popleft(),\
                                dictionary, queue)
new_queue = deque()
scrape_subreddits(searched_subs, reddit, problematic, new_queue)

Lol what does that even mean. I wanted super retard give me super retard. -|-+-|- 163892  -|-+-|-  47
If you're in a gang the statistic should say 'loser' instead of victim. You knew what would happen, you just didn't manage to fight your way out when the time came. It would also make some minority crime statistics a little more palatable. Instead of saying black people are idiots who kill each other, say "black losers kill each other a lot,  so don't be a loser in a gang that makes your race look statistically like dumb tribals". Separation of culture and race in statistics would be handy, but might be so "controversial", it'd get shot down. Because identifying and eliminating cultures is an actual solution, nobody will admit it though, it'd just be seen as Racism 2.0: Discriminate Discrimination. Really if drugs and prostitution were legalized these people would lose all outside support and end up stuck with crimes nobody likes, making them easy to rally against -|-+-|- 163969  -|-+-

Femcels aren't "can't get laid" it is "can't get married". -|-+-|- 165682  -|-+-|-  1837
I can see why people are anti-Zionist, but imagine being a fucking Palestine-supporting cuck. Enjoy strapping bombs to pregnant women dude? -|-+-|- 165789  -|-+-|-  1944
Sorry about that grammar Nazi. -|-+-|- 165872  -|-+-|-  2027
Yeah, having a preference is so evil and hateful. 

Don't be a douchebag -|-+-|- 165907  -|-+-|-  2062
I think I’ll have more white children with my husband. -|-+-|- 165933  -|-+-|-  2088
Because I’m white and people are so mean to me I just can’t take it any more -|-+-|- 165959  -|-+-|-  2114
If this was school I would appreciate it but it seemed like a grammar nazi reply.

Sorry and thanks for the info. -|-+-|- 165985  -|-+-|-  2140
Did your boyfriend dump you for a chapo poster? -|-+-|- 166036  -|-+-|-  2191
With a user name referring to sucking on things I'm just going to assume you are a pole smoker with a thing for young boys and girls. -|-+-|- 166155  -|-+-|-  2310

Thank you! But what’s a women attitude? -|-+-|- 168019  -|-+-|-  4174
How can you rationally believe that people wouldn't report a violent/deadly crime just because someone is white? That's genuinely insane. -|-+-|- 168045  -|-+-|-  4200
Have a nice day :) -|-+-|- 168071  -|-+-|-  4226
Yet here you are! -|-+-|- 168175  -|-+-|-  4330
>I hate Politicians

>A more tyrannical politician? Allow me to lick your boots, sire! -|-+-|- 168247  -|-+-|-  4402
How short is Gwen-Stacy-From-Into-The-Spiderverse short? -|-+-|- 168292  -|-+-|-  4447
Lol I mean you can say racist shit all you want but there are smart and highly skilled immigrants from everywhere.
Usually hen people say shit like this they’re just compensating for personal problems. -|-+-|- 168372  -|-+-|-  4527
If they were skilled labor, America would have fallen apart when slavery had become illegal. -|-+-|- 168398  -|-+-|-  4553
Dirty Chapocel, why don’t you make a fart joke? -|-+-|- 168441  -|-+-|-  4596
what do you mean by that? -|

I can get a bagel, a slice of ham, 6oz of cheese, and 24oz of juice for that -|-+-|- 169653  -|-+-|-  302
> I'd rather not see them or be near them

Audible oof -|-+-|- 169681  -|-+-|-  330
Is the green dude really a dude,

or a victim of the "medical" industry? -|-+-|- 169713  -|-+-|-  362
I mean this sub is just talking about the 2 genders, lgb arnt genders so i was confused lol -|-+-|- 169772  -|-+-|-  421
Here you go: 

https://www.google.com/search?q=bigot

I wonder if you will disregard facts.

**EDIT:** Hahahahaha a downvote and no reply. Yup. Just preserving the lulz in case of triggered deletion... 

/u/mixingu said (about the definition of a bigot):

>>towards those who hold different opinions

>That's not true at all but okay. -|-+-|- 169798  -|-+-|-  447
And only one of us knows you're utterly delusional at this point. My advice: seek help as soon as humanly possible. -|-+-|- 169824  -|-+-|-  473
That's some serious /r/jesuschristreddit or /r/imgoingtohellforthis2 material 

Lol you think you’re a mind-expanding Ascended Master, while you just bang biological males. -|-+-|- 171282  -|-+-|-  1931
Yup. That last sentence exactly. -|-+-|- 171325  -|-+-|-  1974
K. What were the results of those cases? You're still wrong, reeeeeetard. -|-+-|- 171474  -|-+-|-  2123
Sounds like you're the racist and homophobe -|-+-|- 171545  -|-+-|-  2194
Oh I’m wonderful actually. Loving my best life!

Please be well -|-+-|- 171571  -|-+-|-  2220
Google XX Chromosomes -|-+-|- 171608  -|-+-|-  2257
Curious that I'm the only one to have sent a link to any scientific articles at all, despite trying to find out if there's anything other than "I was taught this once and never bothered to challenge my viewpoint. People who claim I'm wrong are just evil and retarded." from people who believe there are only 2 genders an are active on a subreddit dedicated to opposing any other idea. -|-+-|- 171634  -|-+-|-  2283
Lol okay, nice hypothesis, got anything to back that up or do you just like

...

63 million Americans thought this asshole was better than the hillarybot. We deserve whatever nuclear apocolypse this man starts for allowing him to be in a position of power.  -|-+-|- 385524  -|-+-|-  211576
Do you remember the time a member of Congress brought a literal snowball onto the floor to prove to everyone that climate change can't be happening, because he had just gone outside and gotten his little snowball. -|-+-|- 385550  -|-+-|-  211602
Don’t encourage him, he doesn’t understand sarcasm
I’m pretty sure he thinks Mark Hamill beats off to pictures of Trump 
 -|-+-|- 385576  -|-+-|-  211628
He didn't have to take the job. -|-+-|- 385602  -|-+-|-  211654
Man, buying the WTC would have been a HUGE blunder for him... -|-+-|- 385628  -|-+-|-  211680
I agree, at this point, but early on he was constantly at odds with traditional conservatives, and I think the left seemed really determined to guarantee his current entrenchment. 
It’s worth noting, I was no exception... -|-+-|- 385

Hamberder and covefefe  -|-+-|- 387017  -|-+-|-  213069
Been great watching you play every Saturday, best of luck prepping for whatever the future may hold for you! \m/ -|-+-|- 387043  -|-+-|-  213095
you have very long arms -|-+-|- 387069  -|-+-|-  213121
that's hot. -|-+-|- 387095  -|-+-|-  213147
You look like a cross between lonzo ball and Kenny G -|-+-|- 387121  -|-+-|-  213173
How the fuck is your arm longer than you hair -|-+-|- 387147  -|-+-|-  213199
Don't call him that.  -|-+-|- 387173  -|-+-|-  213225
Are you the lovechild of James Franco and Bob Marley?! -|-+-|- 387199  -|-+-|-  213251
Your successful selfie attempt with the failed President of the United States. -|-+-|- 387225  -|-+-|-  213277
That’s too fucking great lol -|-+-|- 387251  -|-+-|-  213303
Thats the most human Ive ever seen him -|-+-|- 387277  -|-+-|-  213329
You seem to be a member of the NDSU football team . How where your hamerders ? -|-+-|- 387303  -|-+-|-  213355
He looks like one of the many QB’s that y

Yeah like an actual traitor and agent of Russia in charge of our executive branch! GOOD TIMES. It's like your coach taking play calls from the other team during the playoffs.  -|-+-|- 389513  -|-+-|-  215565
hilariously tragic -|-+-|- 389539  -|-+-|-  215591
*criticisms can still be valid even if they’re repeated frequently by the majority* -|-+-|- 389565  -|-+-|-  215617
Sure, [https://www.forbes.com/sites/ashleystahl/2017/08/11/why-democrats-should-be-losing-sleep-over-generation-z/#15f92f4d7878](https://www.forbes.com/sites/ashleystahl/2017/08/11/why-democrats-should-be-losing-sleep-over-generation-z/#15f92f4d7878) -|-+-|- 389591  -|-+-|-  215643
Lmao and they each expire when? The alt right always argues in bad faith. -|-+-|- 389617  -|-+-|-  215669
Pretty sure that was meant for the other guy, I'm defending Trump lol -|-+-|- 389643  -|-+-|-  215695
I wish I had such glorious hair. I'll let you guys decide who I'm talking about. -|-+-|- 389669  -|-+-|-  215721
The thing about the k

Wait hold up. You think meeting someone is terrible? Being Civil to someone you dislike is now terrible? This man shaking hands with this (bad) president hurts the people trying to stop him?? How? 

To me in fact it seems to only fuel your rage, I think you are contradicting yourself my dude. 

And getting a chance to talk to someone who is evil does not make you evil. This means you believe by just saying hello to an evil person makes you evil. That is flat out incorrect. Again your logic is, odd.  -|-+-|- 391021  -|-+-|-  217073
Fuck, you got me.  Why else would I be fucking with people who can only be found via sorting by controversial. -|-+-|- 391047  -|-+-|-  217099
I am not talking about special agents -|-+-|- 391073  -|-+-|-  217125
[deleted] -|-+-|- 391099  -|-+-|-  217151
Of course you guys don't. Look up dunning-kruger. Your master is the embodiment of it. -|-+-|- 391125  -|-+-|-  217177
Congrats on your insanity -|-+-|- 391151  -|-+-|-  217203
Here is a link to the transcrip

RequestException: error with request HTTPSConnectionPool(host='oauth.reddit.com', port=443): Max retries exceeded with url: /api/morechildren/?raw_json=1 (Caused by NewConnectionError('<urllib3.connection.VerifiedHTTPSConnection object at 0x7f8bb0189dd0>: Failed to establish a new connection: [Errno -2] Name or service not known'))

In [21]:
def scrape_subreddits(searched_subs, reddit, dictionary, queue):
    '''
    Takes a list of strings representing subreddits, gets the
    controversial posts from each subreddit, then takes the
    comments and adds them to a dictionary.
    
    Parameters:
    -----------
    
    searched_subs: list of str
    reddit: Reddit instance
    dictionary: dict
    queue: deque
    
    Returns:
    --------
    
    None
    
    '''
    for subreddit in searched_subs:
        for sorting in [ lambda sub: reddit.subreddit(subreddit).hot(),
                     lambda sub: reddit.subreddit(sub).new(),
                     lambda sub: reddit.subreddit(sub).top(),
                     lambda sub: reddit.subreddit(sub).controversial()]:
        #subr=reddit.subreddit(subreddit)
        #for submission in subr.controversial():
            for submission in sorting(subreddit):
        
                parse_CommentForest(submission.comments, dictionary,queue)
        while len(queue) >= 1:
            parse_CommentForest(queue.popleft(), dictionary, queue)
        

In [23]:
scrape_subreddits(['pics'],reddit,info,deque())

https://www.reddit.com/r/pics/comments/di2wle/pumpkins_are_ready_to_go/?utm_source=share&utm_medium=ios_app&utm_name=iossmf

Pumpkin carvings! -|-+-|- 88097  -|-+-|-  6
[These Halloween invites.](https://i.imgur.com/iJGiZrs.jpg)

My mother in law made them with Elmer's glue on her toe. Filled it with cotton balls and hot glue. Painted with wood varnish.

Probably the grossest thing I've gotten in the mail. -|-+-|- 88103  -|-+-|-  12
[Oogie Boogie Jack-O-Lantern](https://www.reddit.com/r/pics/comments/dijdi2/girlfriend_made_an_oogie_boogie_jackolantern/?utm_medium=android_app&utm_source=share)
Made by my amazing girlfriend -|-+-|- 88109  -|-+-|-  18
[Ghost people running on the beach before dawn!](https://www.reddit.com/r/pics/comments/dj6aac/ghost_people_running_on_the_beach_before_dawn/) -|-+-|- 88115  -|-+-|-  24
[Tried to make a ghost for Halloween, accidentally made a statue of Mother Mary.](https://imgur.com/gallery/VueVeWJ) -|-+-|- 88121  -|-+-|-  30
[deleted] -|-+-|- 88127  -|-+

Hey man, if you want to sell these stuff, just let me know. I would like to be your first customer. These are great, and you have real talent. Respect -|-+-|- 88670  -|-+-|-  579
Do you sell any of your work? -|-+-|- 88676  -|-+-|-  585
Beautiful work!!! 😍
Also, you're cute 😉
Good luck with your shyness! -|-+-|- 88682  -|-+-|-  591
Dude, your shit is dope! Don’t be shy, you’re gonna be real successful with that stuff. Looks incredible -|-+-|- 88688  -|-+-|-  597
Couldn't open the imgur album for some reason. Are those pens fountain pens? If they are, r/fountainpens would probably appreciate them a lot. -|-+-|- 88694  -|-+-|-  603
Do you send internationally. -|-+-|- 88700  -|-+-|-  609
You should be proud of yourself, those are beautiful looking pieces! Keep up the great work! -|-+-|- 88706  -|-+-|-  615
r/diyaudio 

If you wanna take it another level, you can get really into speaker building through this sub. Also learning about ports and enclosure volumes and tuning is easy -|-+-|- 8

Hold on, I’m going to go set your car on fire and see if you feel the same way. -|-+-|- 89002  -|-+-|-  911
I agree, but I think it's unlikely we are missing something that trumps what we are already looking at (health, life expectancy, education, etc.). -|-+-|- 89008  -|-+-|-  917
I want to watch this animated movie! -|-+-|- 89020  -|-+-|-  929
Love your style. Takes me back to my childhood for some reason. -|-+-|- 89026  -|-+-|-  935
Is that a chimp walking a dog, or just a mutant/cyborg? -|-+-|- 89032  -|-+-|-  941
this is a beautifully done piece, very impressive -|-+-|- 89038  -|-+-|-  947
What details? -|-+-|- 89044  -|-+-|-  953
Just my thought :) -|-+-|- 89050  -|-+-|-  959
Reminds me of the opening to an apocalyptic short film or game -|-+-|- 89056  -|-+-|-  965
That was accurate -|-+-|- 89062  -|-+-|-  971
Clear skies in london? -|-+-|- 89072  -|-+-|-  981
I  hear Arctic Monkeys in this picture -|-+-|- 89078  -|-+-|-  987
Looks like a still from Blade runner. I love the look 

KeyboardInterrupt: 

In [11]:
for k,v in info.items():
    if len(v) == 0:
        print(k)

submission_author


In [13]:
dir(subr)

['MESSAGE_PREFIX',
 'STR_FIELD',
 'VALID_TIME_FILTERS',
 '__class__',
 '__delattr__',
 '__dict__',
 '__dir__',
 '__doc__',
 '__eq__',
 '__format__',
 '__ge__',
 '__getattr__',
 '__getattribute__',
 '__gt__',
 '__hash__',
 '__init__',
 '__init_subclass__',
 '__le__',
 '__lt__',
 '__module__',
 '__ne__',
 '__new__',
 '__reduce__',
 '__reduce_ex__',
 '__repr__',
 '__setattr__',
 '__sizeof__',
 '__str__',
 '__subclasshook__',
 '__weakref__',
 '_create_or_update',
 '_fetch',
 '_fetch_data',
 '_fetch_info',
 '_fetched',
 '_kind',
 '_path',
 '_reddit',
 '_reset_attributes',
 '_safely_add_arguments',
 '_submission_class',
 '_submit_media',
 '_subreddit_collections_class',
 '_subreddit_list',
 '_upload_media',
 '_url_parts',
 '_validate_time_filter',
 'banned',
 'collections',
 'comments',
 'contributor',
 'controversial',
 'display_name',
 'emoji',
 'filters',
 'flair',
 'fullname',
 'gilded',
 'hot',
 'message',
 'mod',
 'moderator',
 'modmail',
 'muted',
 'new',
 'parse',
 'quaran',
 'random

In [29]:
while len(queue) >= 1:
    cf = queue.popleft()
    parse_CommentForest(cf, info, queue)

In [18]:
dir(comment.replies)

['__class__',
 '__delattr__',
 '__dict__',
 '__dir__',
 '__doc__',
 '__eq__',
 '__format__',
 '__ge__',
 '__getattribute__',
 '__getitem__',
 '__gt__',
 '__hash__',
 '__init__',
 '__init_subclass__',
 '__le__',
 '__len__',
 '__lt__',
 '__module__',
 '__ne__',
 '__new__',
 '__reduce__',
 '__reduce_ex__',
 '__repr__',
 '__setattr__',
 '__sizeof__',
 '__str__',
 '__subclasshook__',
 '__weakref__',
 '_comments',
 '_gather_more_comments',
 '_insert_comment',
 '_submission',
 '_update',
 'list',
 'replace_more']

In [11]:
from copy import deepcopy
info = {'author':[], 'url':[],'body':[],'subreddit':[],
        'submission_author':[],'sub_id':[],'comment_id':[],
        'comment_permalink':[],'submission_permalink':[],
        'reference_set':set()}
problematic,backup, backup_info = deepcopy(info),deepcopy(info),deepcopy(info)
i = 0
directory = '/home/justin/.local/share/xdg/media/documents/textfiles/galvanize/slur-prediction/data'

file = 'reddit_data_testing'
j = 2

for subreddit in searched_subs:
    subr = reddit.subreddit(subreddit)
    for submission in subr.search('elon musk'):
        submission.comments.replace_more(limit=None)
        for comment in submission.comments.list():
            if i % 5000 == 0:

                DataFrame(info).to_csv(f'{directory}/{file}_{str(j)}.csv')
                DataFrame(problematic).to_csv(f'{directory}/{file}_problematic_{str(j)}')
                
                
                j += 1
                for keys in info:
                    backup_info[keys].extend(info[keys])
                    backup[keys].extend(problematic[keys])
                    info[keys] = []
                print('info length = ',len(info['author']))
                print('backup length = ',len(backup['author']))
            
            for terms in slurs:
                if terms in comment.body and terms not in not_conditions:
                    if not comment.author:
                        problematic['author'].append('None')
                    else:
                        problematic['author'].append(comment.author.name)
                    problematic['body'].append(comment.body)
                    problematic['subreddit'].append(submission.subreddit.display_name)
                    problematic['submission_author'].append(submission.author_fullname)
                    problematic['sub_id'].append(submission.id)
                    problematic['url'].append(submission.url)
                    problematic['comment_id'].append(comment.id)
                    problematic['comment_permalink'].append(comment.permalink)
                    problematic['submission_permalink'].append(submission.permalink)
                else:
                    if not comment.author:
                        info['author'].append('None')
                    else:
                        info['author'].append(comment.author.name)
                    info['body'].append(comment.body)
                    info['subreddit'].append(submission.subreddit.display_name)
                    info['submission_author'].append(submission.author_fullname)
                    info['sub_id'].append(submission.id)
                    info['url'].append(submission.url)
                    info['comment_id'].append(comment.id)
                    info['comment_permalink'].append(comment.permalink)
                    info['submission_permalink'].append(submission.permalink)


            i += 1

info length =  0
backup length =  0


KeyboardInterrupt: 

In [232]:
day = 'tue'
j='total'
DataFrame(backup).to_csv(f'{directory}/{day}/{file}_{str(j)}.csv')
DataFrame(backup).shape

(45000, 9)

In [ ]:
type(c)

In [243]:
from pandas import read_csv
reddit_data = read_csv(f'{directory}/{day}/reddit_data_total.csv')

In [252]:
for user in list(reddit_data['author'].unique()):
    for comments in reddit.redditor(user).comments.new(limit=None):
        if 'elon' in comments.body.lower() or 'musk' in comments.body.lower():
            if comments.controversiality != 0:
                print(comments.controversiality)
                print(comments.body)

1
The money belonged to another account. That's why it's theft. Let's say you live in an apartment and the UPS guy drops off a valuable ring in your mailbox instead of your neighbors. You still stole a ring
1
One person's fact is another person's smear. Here are facts about his jet travel in 2018, do you think it is a smear?

*Elon Musk’s highflying 2018: What 150,000 miles in a private jet reveal about his ‘excruciating’ year*

*Tesla chief Elon Musk’s corporate jet flew more than 150,000 miles last year, or more than six times around the Earth, as he raced between the outposts of his futuristic empire during what he has called “the most difficult and painful year” of his career, according to flight records obtained by* [The Washington Post](https://www.washingtonpost.com/business/economy/elon-musks-highflying-2018-what-150000-miles-in-a-private-jet-reveal-about-his-excruciating-year/2019/01/29/83b5604e-20ee-11e9-8b59-0a28f2191131_story.html).

Leading by example on Climate Change!   

1
Freddie @ Electrek pipes in:  Tesla increases cost of using its Supercharger stations, still says it ‘will never be a profit center’

>Those are some surprisingly steep increases, but the good news is that it still for the most part significantly less expensive than gasoline.

>We also need to keep in mind that Superchargers are not the main way to charge for the vast majority of Tesla owners at the moment. Home charging is the main way for most people to charge and the cost of that is solely dependent on your local electricity rates.

>Tesla’s Superchargers are generally used for long distance travel. (yapyap2: ROFL)

>In general, I don’t have an issue with Tesla increasing the rates here, but it does raise some questions about Tesla’s promised $0.07 per kWh for Tesla Semi customers at the upcoming Megachargers.

>That’s a hard price to achieve in the first place, but if Tesla plans to achieve that with the Megachargers, I don’t see any reason why they couldn’t achieve a similar rat

1
They can't imagine driving conditions outside of California (because after all, who lives anywhere else?) and they didn't think testing these cars was worth the time. That's because Musk thinks he knows more than all the other car company CEO's. It's hilarious. A genuine laugh riot. 
1
As I had said numerous times (I, II, III, IV), Tesla lags massively on full self-driving technology. The leader when it comes to self-driving is Google GOOGL, with General Motors also producing good work under very trying conditions.

However, the only company selling FSD (Full Self-Driving) cars is, and has been (since October 2016), Tesla. That is, Tesla has been selling cars with the promise they’ll be able to self-drive for nearly 1 year and 3 months (1.25 years).

Given this fact, both the market and the customers buying these cars might be interested in knowing when Tesla will deliver what it has been selling. This is all the more important, because:

Tesla doesn’t just sell cars outright with th

1
His "autopilot" just might break his company. In a sane and rational world (ROFL) NHTSA and/or the NTSB would order this extremely dangerous BETA software disabled and they would fine this company for endangering the public.   

Even the faithful are tiring of this charade, here's AmpedRealtor from the Tesla Motors Club forum, an owner and former apologist:  

>There is, it's called a lawsuit. It's already been filed and I can bet that Tesla will offer full refunds as a settlement. Tesla made its bed here. They made promises they couldn't fulfill and continue to make promises they cannot come remotely close to delivering. They keep digging themselves deeper into this hole, and I can only assume it's due to the over confidence and hubris of Musk.  

>Karpathy, the new head of Autopilot or whatever he is, says "Delivering autonomy at scale". What a bunch of nonsense! Tesla is no more delivering autonomy than they are pizzas. Tesla is really screwing itself by handling Autopilot as if i

1
I’m just saying that Tesla’s timelines always extend much further than whatever Elon tweets

It wasn’t meant to be taken literally
1
Cant say anything about daddy musk, his lifestyle company really makes people believe theyre making a change and they cant imagine being duped
1
The DNC has shut down the green new deal. Theyve continued to either pay lip service to or simply ignore the climate crisis without offering any substantive policies, save for a few progressive ones (all of whom hardly have the support of the establishment). 

Think about it- even if fossil fuel companies dont donate to democrat candidates, they still need to out their money somewhere, probably in a bank. Banks also want to invest in profitable businesses, and fossil fuels are pretty lucrative. Everyone in the upper echelons in this economy has a vested interest in perpetuating the use fossil fuels, and those same people donate *heavily* to democrat candidates. Idk what we can do with this current political lan

KeyboardInterrupt: 

In [280]:
user_info = {}
def get_controversial(user):
    return reddit.redditor(user).comments.controversial(limit=None)
def get_hot(user):
    return reddit.redditor(user).comments.hot(limit=None)
def get_new(user):
    return reddit.redditor(user).comments.new(limit=None)
def get_top(user):
    return reddit.redditor(user).comments.controversial(limit=None)
for z in [get_top, get_controversial, get_new]:
    for comments in z(user):
        break

In [284]:
'created':[], 'author':[],'score':[],'submission':[], 'subreddit:[]'
    comments.created
    comments.author
    comments.score
    comments.submission
    comments.subreddit
dir(comments)

['MISSING_COMMENT_MESSAGE',
 'STR_FIELD',
 '__class__',
 '__delattr__',
 '__dict__',
 '__dir__',
 '__doc__',
 '__eq__',
 '__format__',
 '__ge__',
 '__getattr__',
 '__getattribute__',
 '__gt__',
 '__hash__',
 '__init__',
 '__init_subclass__',
 '__le__',
 '__lt__',
 '__module__',
 '__ne__',
 '__new__',
 '__reduce__',
 '__reduce_ex__',
 '__repr__',
 '__setattr__',
 '__sizeof__',
 '__str__',
 '__subclasshook__',
 '__weakref__',
 '_extract_submission_id',
 '_fetch',
 '_fetch_data',
 '_fetch_info',
 '_fetched',
 '_kind',
 '_reddit',
 '_replies',
 '_reset_attributes',
 '_safely_add_arguments',
 '_submission',
 '_url_parts',
 '_vote',
 'all_awardings',
 'approved_at_utc',
 'approved_by',
 'archived',
 'author',
 'author_flair_background_color',
 'author_flair_css_class',
 'author_flair_richtext',
 'author_flair_template_id',
 'author_flair_text',
 'author_flair_text_color',
 'author_flair_type',
 'author_fullname',
 'author_patreon_flair',
 'banned_at_utc',
 'banned_by',
 'block',
 'body',
 'b

In [290]:
comments.subreddit.display_name

'FortniteCompetitive'

In [205]:
from pandas import DataFrame
reddit_data=DataFrame(info)
DataFrame(info).to_csv('test_file.csv')

In [231]:
from datetime import datetime
print(datetime.utcfromtimestamp(comment.created).strftime('%A, %e %B %Y\nat %H:%M:%S'))

Friday, 13 July 2018
at 09:00:59


In [204]:
!cat '/home/justin/.local/share/xdg/media/documents/textfiles/galvanize/w4/tue/reddit_data.csv'

,author,url,body,subreddit,submission_author,sub_id,comment_id,comment_permalink,submission_permalink
0,Amamazing,https://www.bbc.com/news/world-us-canada-48238576?intlink_from_url=&link_location=live-reporting-story,"From article:

The federal court judge set a 22 October trial date.

Mr Musk is being sued by Vern Unsworth, who helped rescue the 12 boys from Thailand's Tham Luang caves.

The Tesla boss called Mr Unsworth a ""pedo"" in a Twitter post after the Briton said Mr Musk's attempt to help in the rescue was a ""PR stunt"".",news,t2_1upquyef,bnfkry,en53myv,/r/news/comments/bnfkry/elon_musk_must_defend_himself_in_court_after/en53myv/,/r/news/comments/bnfkry/elon_musk_must_defend_himself_in_court_after/
1,melodypowers,https://www.bbc.com/news/world-us-canada-48238576?intlink_from_url=&link_location=live-reporting-story,Musk was a fucking idiot with this. Why? Just why? The entire world was watching the drama about these boys. We wanted heros to save them. And then they did. Even i

657,monster_mentalissues,https://www.bbc.com/news/world-us-canada-48238576?intlink_from_url=&link_location=live-reporting-story,And all the offences occurred in America. Hence why the court case is here. Pretty simple.,news,t2_1upquyef,bnfkry,en6f84d,/r/news/comments/bnfkry/elon_musk_must_defend_himself_in_court_after/en6f84d/,/r/news/comments/bnfkry/elon_musk_must_defend_himself_in_court_after/
658,half3clipse,https://www.bbc.com/news/world-us-canada-48238576?intlink_from_url=&link_location=live-reporting-story,"> wherever damages for defamation would occur

Which is anywhere defamation occurs. The very act causes damages, even assuming there are no other losses like employment being effected.

Which means he could sue musk in every country that twitter has a presence, or at least could show that someone there read the tweet. Damages from defamation absolutely occured in america. You coudl also define is as occuring on twiter, which is a platform run by a company that's incorprated in

1418,tanafras,https://www.mlive.com/news/flint/2018/12/elon-musk-provides-423k-to-buy-laptops-for-all-flint-middle-schoolers.html,"Great, now they can steal and sell them for water.",news,t2_kauvf,a7yjzk,ec7qh4f,/r/news/comments/a7yjzk/elon_musk_provides_423k_to_buy_laptops_for_all/ec7qh4f/,/r/news/comments/a7yjzk/elon_musk_provides_423k_to_buy_laptops_for_all/
1419,None,https://www.mlive.com/news/flint/2018/12/elon-musk-provides-423k-to-buy-laptops-for-all-flint-middle-schoolers.html,Props to Musk - dudes like this need to be president.....not orange clowns ,news,t2_kauvf,a7yjzk,ec7qok0,/r/news/comments/a7yjzk/elon_musk_provides_423k_to_buy_laptops_for_all/ec7qok0/,/r/news/comments/a7yjzk/elon_musk_provides_423k_to_buy_laptops_for_all/
1420,watchtheworldbrn,https://www.mlive.com/news/flint/2018/12/elon-musk-provides-423k-to-buy-laptops-for-all-flint-middle-schoolers.html,"I guess trickle down does work /s. But really, i guess this is good to hear.",news,t2_kauvf,a7yjzk,ec7qqkw,/r/news

2645,grelo29,https://www.mlive.com/news/flint/2018/12/elon-musk-provides-423k-to-buy-laptops-for-all-flint-middle-schoolers.html,"Hey guy. Happy to hear from you. Flint, Michigan is having a water issue. It’s not a country issue. They’ve been without clean water for a long time now. Welcome to reddit. ",news,t2_kauvf,a7yjzk,ec7eow2,/r/news/comments/a7yjzk/elon_musk_provides_423k_to_buy_laptops_for_all/ec7eow2/,/r/news/comments/a7yjzk/elon_musk_provides_423k_to_buy_laptops_for_all/
2646,sabttolf,https://www.mlive.com/news/flint/2018/12/elon-musk-provides-423k-to-buy-laptops-for-all-flint-middle-schoolers.html,Then he will deduce 80% of it from his taxes anyways. and the free publicity this provides will cover it anyway.,news,t2_kauvf,a7yjzk,ec73os4,/r/news/comments/a7yjzk/elon_musk_provides_423k_to_buy_laptops_for_all/ec73os4/,/r/news/comments/a7yjzk/elon_musk_provides_423k_to_buy_laptops_for_all/
2647,sabttolf,https://www.mlive.com/news/flint/2018/12/elon-musk-provides-423k-to-buy-lapt

3567,None,https://www.mlive.com/news/flint/2018/12/elon-musk-provides-423k-to-buy-laptops-for-all-flint-middle-schoolers.html,[deleted],news,t2_kauvf,a7yjzk,ec7haa7,/r/news/comments/a7yjzk/elon_musk_provides_423k_to_buy_laptops_for_all/ec7haa7/,/r/news/comments/a7yjzk/elon_musk_provides_423k_to_buy_laptops_for_all/
3568,High_Speed_Idiot,https://www.mlive.com/news/flint/2018/12/elon-musk-provides-423k-to-buy-laptops-for-all-flint-middle-schoolers.html,I'm just reminding people that this amount is a rounding error to Musk and an incredibly meaningful amount to the people he gave it to. Good on him.  ,news,t2_kauvf,a7yjzk,ec75oxx,/r/news/comments/a7yjzk/elon_musk_provides_423k_to_buy_laptops_for_all/ec75oxx/,/r/news/comments/a7yjzk/elon_musk_provides_423k_to_buy_laptops_for_all/
3569,aptwo,https://www.mlive.com/news/flint/2018/12/elon-musk-provides-423k-to-buy-laptops-for-all-flint-middle-schoolers.html,"I guess the point didn't cross your mind at all. It's ok, people like you never reall

...

30325,yupyepyupyep,http://www.fox5atlanta.com/news/elon-musk-pledges-to-fund-fixing-water-in-flint-homes-contaminated-above-fda-levels,"At least you didn't call me ""pedo guy"".",news,t2_jl7ph4h,8y4eg8,e2hgem0,/r/news/comments/8y4eg8/elon_musk_pledges_to_fix_flint_mi_water_problem/e2hgem0/,/r/news/comments/8y4eg8/elon_musk_pledges_to_fix_flint_mi_water_problem/
30326,Icyburritto,http://www.fox5atlanta.com/news/elon-musk-pledges-to-fund-fixing-water-in-flint-homes-contaminated-above-fda-levels,"Oh yeah, I know musk isn’t the only one. I’m just amazed that it his guy seems to be picking up where the government quits. Space exploration, bullet trains, electric cars. He accepts challenges and completes them. It’s really admirable I think (although he makes billions doing it)",news,t2_jl7ph4h,8y4eg8,e28j8qu,/r/news/comments/8y4eg8/elon_musk_pledges_to_fix_flint_mi_water_problem/e28j8qu/,/r/news/comments/8y4eg8/elon_musk_pledges_to_fix_flint_mi_water_problem/
30327,improbable_humanoid,http:/

30614,DaedricRob,http://www.fox5atlanta.com/news/elon-musk-pledges-to-fund-fixing-water-in-flint-homes-contaminated-above-fda-levels,SO TRUE. Holy shit we only ever *hear* about these annoying fans. There needs to be a new word for fan-of-popular-thing haters.,news,t2_jl7ph4h,8y4eg8,e28ml93,/r/news/comments/8y4eg8/elon_musk_pledges_to_fix_flint_mi_water_problem/e28ml93/,/r/news/comments/8y4eg8/elon_musk_pledges_to_fix_flint_mi_water_problem/
30615,RJrules64,http://www.fox5atlanta.com/news/elon-musk-pledges-to-fund-fixing-water-in-flint-homes-contaminated-above-fda-levels,"It's because people get a distorted view of a person on Reddit, because we usually only see a user comment once, in our whole life. And we attach that username to that one comment.

I've seen it happen to myself.

In the last week, I made a few comments defending what I thought were unfair attacks on Musk. I was called a dick sucking cock riding fanboy who's blinded by his love for an idol.

The next day, I made a com

30881,Shatners_Balls,http://www.fox5atlanta.com/news/elon-musk-pledges-to-fund-fixing-water-in-flint-homes-contaminated-above-fda-levels,"> than an individual.  

Are you suggesting we return to the Monarchy? UK would be glad to hear it. ",news,t2_jl7ph4h,8y4eg8,e29664l,/r/news/comments/8y4eg8/elon_musk_pledges_to_fix_flint_mi_water_problem/e29664l/,/r/news/comments/8y4eg8/elon_musk_pledges_to_fix_flint_mi_water_problem/
30882,You_re_Next,http://www.fox5atlanta.com/news/elon-musk-pledges-to-fund-fixing-water-in-flint-homes-contaminated-above-fda-levels,"That's a fine mischaracterization. Republicans have issues with welfare and over-regulation. They like infrastructure and proper law enforcement. 

What you said is the equivalent of saying : Democrats dream of American Soldiers sleeping on the streets because they want to cut military spending. ",news,t2_jl7ph4h,8y4eg8,e2iowpy,/r/news/comments/8y4eg8/elon_musk_pledges_to_fix_flint_mi_water_problem/e2iowpy/,/r/news/comments/8y4eg8/elon_

To add a second edit: you say they couldn’t treat that wasn’t the issue. Why were they building a phosphate system to add mineral to the protective layer to combat the issue then? They certainly could of treated the water and corrected it and made it safe so the leeching didn’t occur but they did it too little too late. This has come out in the trials. Detroit free press is all over it. ",news,t2_jl7ph4h,8y4eg8,e28dl8r,/r/news/comments/8y4eg8/elon_musk_pledges_to_fix_flint_mi_water_problem/e28dl8r/,/r/news/comments/8y4eg8/elon_musk_pledges_to_fix_flint_mi_water_problem/
31082,Raptorheart,http://www.fox5atlanta.com/news/elon-musk-pledges-to-fund-fixing-water-in-flint-homes-contaminated-above-fda-levels,They had to treat it when they switched from Detroit water the first time to prevent the leeching,news,t2_jl7ph4h,8y4eg8,e28btvy,/r/news/comments/8y4eg8/elon_musk_pledges_to_fix_flint_mi_water_problem/e28btvy/,/r/news/comments/8y4eg8/elon_musk_pledges_to_fix_flint_mi_water_problem/
31083,

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [149]:
for c in comment.comments():
    if type(c).__name__ == 'MoreComments':
        parse_comments(c.comments(update=True))
    else:
        print(c.author)

LUL__XD
Kupy
VegasKL
Koa914914914
tyranid1337
WolfStudios1996

That’s why we must see to it that he stays in power indefinitely.
MutantOctopus
Damassteel_ironworks
Pesticide001
Damassteel_ironworks

Yeah, like nobody is allowed to make a mistake, ever. What a great society that would be. 
You probably never said, wrote or did anything wrong, amirite?
Pesticide001

urwrong, calling someone a pedophile in public when u have millions of followers, is almost a death sentence affecting that persons health, mental wellbeing, job and life. its not a 'mistake' its deliberate attempt of persona murder aka character assasination, well defined by the law, and should be punished by any means necessary to undo the damage done
Damassteel_ironworks

Oh shut up and get off of your high horse. You can’t judge that man. 
You just stand on the sideline pointing your finger and scream your head off.
Pesticide001

thats how a just society works, the court of public opinion, go crawl back in ur hole back in

In [ ]:
reddit_dict = {'user':[],'body':[],'id':[]}

In [159]:
def parse_comments(comments):
    if type(comment).__name__ == 'MoreComments':
        parse_comments(comment.comments(update=True))
    else:
        print(comment.author)
        print()
        print(comment.body)

In [126]:
from requests.auth import HTTPBasicAuth
from requests import post

In [ ]:
from json import load
from requests import post
from requests.auth import HTTPBasicAuth

class RedditScraper:
    def __init(self):
        
        with open('/home/justin/.local/cache/reddit/info','r') as creds:
            info = load(creds)
            self.client_id = info['ID']
            self.client_secret = info['SECRET']
            self.user_agent = info['AGENT']
            self.username = info['USER']
            self.password = info['PASS']
        self.get_token()
        se
    def get_token(self):
        client_auth = HTTPBasicAuth(self.client_id, self.client_secret)
        post_data = {'grant_type':'password','username':self.username,'password':self.password}
        headers = {'User-Agent':self.user_agent}
        response = post('https://www.reddit.com/api/v1/access_token',auth=client_auth, data=post_data, headers=headers)
        self.token = response.json()['access_token']
            
            